### Bernoulli and Todd numbers

This nb provides **PyM** functions to compute the Todd numbers and ordinary and higher order Bernoulli numbers.

*Motivations*: (1) Important role in intersection theory; (2) The puzzle of Atiyah's formulas in one of his latest preprints (*The fine structure constant*, 2018):

&#1046; $= \lim_{n\to\infty,\ j\to\infty}{2^{-2n}B^n_{k(j)}}$, where $k(j)=2^{k(j-1)}$ and

&#1046; $=\frac{\pi}{\gamma\log2}\lim_{n\to\infty}\sum_{j=1}^n \frac{1}{2^{j+1}}(j \log j-j +\frac{\log j+1}{j})$,

where &#1046; was supposed to be a mathematical formula for the inverse of the *fine structure constant*:
$$
\alpha=\frac{1}{4\pi\varepsilon_0}\frac{e^2}{\hbar c},\quad 1/\alpha = 137.035 999 084(21).
$$



In [1]:
from PyM import *

#### Auxiliary functions

**`vprod(x,y,d)`**

If vectors `x` and `y` have lengths `r` and `s`, this fucntion returns the first `d` components of the vector of coefficients, starting with degree 1, of the $t$-polynomial $(1+x_1t+\cdots+x_rt^r)(1+y_1t+\cdots+y_st^s)$. By default, `d=r+s`.

**`vpower(x,m,d)`**

Returns the vector of the first `d` coefficients, starting with degree 1,
of the $t$-polynomial $(1+x_1t+\cdots+x_rt^r)^m$. By default, $d=rm$.

In [2]:
def vprod(x,y,d=''):
    if d=='': d = len(x)+len(y)
    if d==0: return []
    z = d*[0]
    for j in range(min(d,len(y))): z[j]=y[j]
    for j in range(min(d,len(x))):
        z[j] += x[j]
        for k in range(min(d-1-j,len(y))):
            z[j+k+1] += x[j]*y[k]
    return vector(z)
    
def vpower(x,m,d=''):
    if d=='': d=len(x)*m
    if m==0: return []
    if m==1: return pad(x,d)
    z = m*[0]    # 1 as t-polynomial
    while m>0:
        if m%2: z = vprod(z,x,d)
        x = vprod(x,x,d)
        m = m//2
    return vector(z)

x = [1,2,3]
y = [7,8,9,10]

show(vprod(x,y))
show(vprod(x,y,10))
show(vprod(x,y,5))

show(vpower(x,2))
show(vpower(x,3,12))
show(len(vpower(y,100)))


[8, 17, 34, 56, 52, 47, 30] 

[8, 17, 34, 56, 52, 47, 30, 0, 0, 0] 

[8, 17, 34, 56, 52] 

[2, 5, 10, 10, 12, 9] 

[3, 9, 22, 36, 57, 71, 63, 54, 27, 0, 0, 0] 

400 



**`invert_vector(c,d)`**

Given a list or vector $[c_1,...,c_r]$, and an integer $d\ge 0$, this function computes the list or vector  
of the first $d$ coefficients, starting with degree 1, of the power series
$(1+c_1t+\cdots+c_rt^r)^{-1}$, which is equivalent to find the inverse of $1+c_1 t+\cdots+c_rt^r$
mod $t^{d+1}$. By default, $d=r$.


In [3]:
def invert_vector(c, d=''): 
    if isinstance(c,Vector_type): return vector(invert_vector(list(c),d))
    if len(c)==0: return invert_vector([0],d)
    if d==0: return []
    if d=='': d=len(c)
    c = pad(c,d)
    s = [-c[0]]
    if d==1: return s
    for k in range(1,d):
        s += [-c[k]-convolution(s,c,k-1)]
    return s 

x = vector([3,-1,1])
y = invert_vector(x)

show('y =',y)

show(vprod(x,invert_vector(x,15),10))
show(vprod(x,invert_vector(x,15),18))
 

y = [-3, 10, -34] 

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0] 

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -258371689, 98950096, -76374088] 



#### Bernoulli numbers

They are defined as the coefficients of the Taylor series of 
$$t/(e^{t}-1):
1/(1+\frac{1}{2!}x+\frac{1}{3!}x^2+\frac{1}{4!}x^3+\cdots)
$$

In [4]:
def bernoulli_numbers(N):
    u = 1>>Q_
    if N==0: return [u]
    B = invert_vector([u/factorial(j+1) for j in range(1,N+1)])
    return [u]+[factorial(k+1)*B[k] for k in range(N)]
#
BV_ = bernoulli_numbers

def bernoulli_number(N):
    if N==0: return 1>>Q_
    elif N==1: return -1/2>>Q_
    else:
        if odd(N): return 0>>Q_
        else: return bernoulli_numbers(N)[-1]
#
B_=bernoulli_number

show('BV_(20) =',bernoulli_numbers(20))

show('B_(100) =',B_(100))
   

BV_(20) = [1, -1/2, 1/6, 0, -1/30, 0, 1/42, 0, -1/30, 0, 5/66, 0, -691/2730, 0, 7/6, 0, -3617/510, 0, 43867/798, 0, -174611/330] 

B_(100) = -94598037819122125295227433069493721872702841533066936133385696204311395415197247711/33330 



#### Todd numbers

They are defined as the coefficients of the Taylor series of 
$$x/(1-e^{-x}):
1/(1-\frac{1}{2!}x+\frac{1}{3!}x^2-\frac{1}{4!}x^3+\cdots)=
1+\frac{1}{2}x+\frac{1}{12}-\frac{1}{720}x^4+\frac{1}{30240}x^6+\cdots
$$

$1, 1/2, 1/12, 0, -1/720, 0, 1/30240, 0, -1/1209600, 0, 1/47900160, 0,$ 

$-691/1307674368000, 0, 1/74724249600, 0, 
-3617/10670622842880000, 0$, 

$43867/5109094217170944000, 0, 
-174611/802857662698291200000$, ...

In [5]:
def todd_numbers(N):
    u = 1>>Q_
    return [1]+invert_vector(witdual([u/factorial(j+1) for j in range(1,N+1)]))

show(todd_numbers(21))


[1, 1/2, 1/12, 0, -1/720, 0, 1/30240, 0, -1/1209600, 0, 1/47900160, 0, -691/1307674368000, 0, 1/74724249600, 0, -3617/10670622842880000, 0, 43867/5109094217170944000, 0, -174611/802857662698291200000, 0] 



#### Higher order Bernoulli numbers $B(n,k)=B^n_k$

In [10]:
def high_bernoulli_numbers(N,k):
    u = 1>>Q_
    if N==0: return [u]
    B = invert_vector([u/factorial(j+1) for j in range(1,N+1)])
    B = vpower(B,k,N)
    return [u]+[factorial(j+1)*B[j] for j in range(N)]
#    
HBs_=high_bernoulli_numbers

def HB_(n,k): return HBs_(n,k)[-1]

show(HB_(5,4))

N=10
for p in [2*j+1 for j in range(1,N+1,2) if is_prime(2*j+1)]:
    show(p**3,HB_(p+2,p+1))

show(HB_(4,3))

show(HB_(3,3)-3**2/2,HB_(5,5)-5**2/2)


-9 

27 -9 

343 -114562/5 

1331 -24466579093/70 

6859 -161867055619224199787/66 

19/10 

-27/4 -625/12 



**Note.** It is known (Carlitz theorem, 1951) that $B(p+2,p+1)$ is divisible by $p^3$
for all prime numbers $p$. Example: $HB\_(5,4)=-9$ is divisible by $3^2$.
Note that $B(2+2,2+1) = 19/10$.

It also happens that $B(p,p)-p^2/2$ is divisible by $p^3$ for $p>=3$.

These and other properties provide good tests for the soundnes of the computations.

In [7]:
def bernoulli_polynomial(n,x='x'):
    u = 1>>Q_
    [Qx,x] = polynomial_ring(Q_,x)
    P = x**n+n*B_(1)*x**(n-1)
    ntop = n
    if even(ntop): ntop+=1
    for k in range(2,ntop,2):
        P += binom(n,k)*B_(k)*x**(n-k)
    return P
#
BP_ = bernoulli_polynomial

k =6;
B= bernoulli_polynomial(k,'x')

show(B)
show(B_(k))


1/42 + (-1/2)*x**2 + (5/2)*x**4 - 3*x**5 + x**6 

1/42 



#### Atiyah's &#1046; $= \lim_{n\to\infty,\ j\to\infty}{2^{-2n}B^n_{k(j)}}$, where $k(j)=2^{k(j-1)}$.

In [8]:
def zhe(n,j):
    if igcd(j,2*n)!=1: return 'zhe: coprime condition not satisfied'
    k=0
    for _ in range(j):
        k=2**k
        #print(k)
    #print(k)
    return HB_(n,k)/(2**(2*n))

N = [n for n in range(1,10) if igcd(n,3)==1 and igcd(n,5)==1]

for n in N: print(abs(zhe(n,3)))

print()
    
for n in N: print(abs(zhe(n,5)))


1/2
11/48
251/7680
11/49152
199/1179648

8192
201325568/3
67551932831498272/15
7426846898319306401956659200/3
14601255254698637346817666327625731/720


#### &#1046; $=\frac{\pi}{\gamma\log2}\lim_{n\to\infty}\sum_{j=1}^n \frac{1}{2^{j+1}}(j \log j-j +\frac{\log j+1}{j})$

In [9]:
from math import pi,log
euler_gamma=0.577215664901532
kappa = pi/euler_gamma/log(2)

def atiyah(n):
    def t(j):
        x = (j*log(j)-j+(log(j)+1)/j)/log(2)
        return (1-x)/2**(j+1)
    s = sum([t(j) for j in range(1,n+1)])
    return s*kappa

print(atiyah(50))
print(atiyah(100))
print(atiyah(200))




0.23120602303795385
0.23120602303718477
0.23120602303718477
